In [6]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

import keras
from keras.layers import Dense, Dropout, Input
from keras.optimizers import Adam
from keras.models import Model, Sequential
from keras.layers.advanced_activations import LeakyReLU
from keras.datasets import mnist

from tqdm import tqdm

In [7]:
# Defining the optimizer 

adam_opt = Adam(lr=0.0002)


In [8]:
# MNIST Dataset
# 60,000 images of size 28x28
# Input: Flattened image (784 features)

def load_data():
    (x_train, y_train), (x_test, y_test) = mnist.load_data()
    x_train = (x_train.astype(np.float32) - 127.5)/127.5 #Normalization to have values b/w -1 to 1
    x_test = (x_test.astype(np.float32) - 127.5) / 127.5
    
    # convert shape of x_train from (60000, 28, 28) to (60000, 784) 
    x_train = x_train.reshape(60000, 784)
    x_test = x_test.reshape(10000, 784)
    
    return (x_train, y_train, x_test, y_test)


(X_train, y_train, X_test, y_test)=load_data()
print(X_train.shape, X_test.shape)

(60000, 784) (10000, 784)


In [9]:
# Input for each image: 784 (flattened image vector)
# Structure: Dense-> Leaky Relu-> Dropout-> Dense-> Leaky Relu-> Dropout-> Dense-> Leaky Relu-> Sigmoid
# Output: P(real_dataset)

def discriminator():
    
    discriminator=Sequential()
    
    discriminator.add(Dense(units = 1024, input_dim=784))
    discriminator.add(LeakyReLU(0.2))
    discriminator.add(Dropout(0.3))
    
    discriminator.add(Dense(units = 512))
    discriminator.add(LeakyReLU(0.2))
    discriminator.add(Dropout(0.3))
    
    discriminator.add(Dense(units = 256))
    discriminator.add(LeakyReLU(0.2))
    
    discriminator.add(Dense(units=1, activation='sigmoid'))

    discriminator.compile(loss='binary_crossentropy', optimizer=adam_opt)
    
    return discriminator    


In [10]:

d = discriminator()
d.summary()

Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_5 (Dense)              (None, 1024)              803840    
_________________________________________________________________
leaky_re_lu_4 (LeakyReLU)    (None, 1024)              0         
_________________________________________________________________
dropout_3 (Dropout)          (None, 1024)              0         
_________________________________________________________________
dense_6 (Dense)              (None, 512)               524800    
_________________________________________________________________
leaky_re_lu_5 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dropout_4 (Dropout)          (None, 512)               0         
_________________________________________________________________
dense_7 (Dense)              (None, 256)              

In [11]:
# Input for each image: latent variable
# Structure: Dense-> Leaky Relu-> Dense-> Leaky Relu-> Dense-> Leaky Relu-> TanH
# Output: 784 (flattened image vector)

#note how we use Tanh as the activation funstion to bring output in the range -1 to 1 which is also the range of our input image in discriminator

def generator():
    generator = Sequential()
    
    generator.add(Dense(units=256,input_dim=100))
    generator.add(LeakyReLU(0.2))
    
    generator.add(Dense(units=512))
    generator.add(LeakyReLU(0.2))
    
    generator.add(Dense(units=1024))
    generator.add(LeakyReLU(0.2))
    
    generator.add(Dense(units=784, activation='tanh'))
    
    generator.compile(loss='binary_crossentropy', optimizer=adam_opt)
    
    return generator

    

In [12]:
g = generator()
g.summary()

Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_9 (Dense)              (None, 256)               25856     
_________________________________________________________________
leaky_re_lu_7 (LeakyReLU)    (None, 256)               0         
_________________________________________________________________
dense_10 (Dense)             (None, 512)               131584    
_________________________________________________________________
leaky_re_lu_8 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dense_11 (Dense)             (None, 1024)              525312    
_________________________________________________________________
leaky_re_lu_9 (LeakyReLU)    (None, 1024)              0         
_________________________________________________________________
dense_12 (Dense)             (None, 784)              

In [13]:
# Noise to be sent to the generator as input
# The random noise will be sampled from a normal distribution with mean 0 and variance 1
# Generates a 1-d vector of gaussian sampled random values

def create_noise(batch_size):  
    return np.random.normal(0,1, [batch_size, 100])
    

In [14]:
def create_gan(discriminator, generator):
    
    discriminator.trainable=False
    
    #input to generator
    gan_input = Input(shape=(100,))
    x = generator(gan_input)
    
    #output of dicriminator with generated input
    gan_output= discriminator(x)
    
    gan= Model(inputs=gan_input, outputs=gan_output)
    gan.compile(loss='binary_crossentropy', optimizer='adam')
    
    return gan

In [15]:
gan = create_gan(d,g)
gan.summary()

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 100)               0         
_________________________________________________________________
sequential_3 (Sequential)    (None, 784)               1486352   
_________________________________________________________________
sequential_2 (Sequential)    (None, 1)                 1460225   
Total params: 2,946,577
Trainable params: 1,486,352
Non-trainable params: 1,460,225
_________________________________________________________________


In [16]:
def plot_generated_images(epoch, generator, examples=100, dim=(10,10), figsize=(10,10)):
    noise= np.random.normal(loc=0, scale=1, size=[examples, 100])
    generated_images = generator.predict(noise)
    generated_images = generated_images.reshape(100,28,28)
    plt.figure(figsize=figsize)
    for i in range(generated_images.shape[0]):
        plt.subplot(dim[0], dim[1], i+1)
        plt.imshow(generated_images[i], interpolation='nearest')
        plt.axis('off')
    plt.tight_layout()
    plt.savefig('gan_generated_image %d.png' %epoch)

In [17]:
def training(epochs=400, batch_size=128):
    
    #load data
    (X_train, y_train, X_test, y_test) = load_data()
    batch_count = X_train.shape[0] / batch_size
    
    #Creating GAN
    gen= generator()
    disc= discriminator()
    gan = create_gan(disc, gen)
    
    for i in range(epochs):
        #To visualize the process
        for _ in tqdm(range(batch_size)):
            noise = create_noise(batch_size)
            
            #Generate fake images
            fake_image = gen.predict(noise)
            
            print(fake_image.shape)
            
            #We need to create batches of data that contain fake images from Generator and real images from the MNIST dataset that we will feed to Discriminator
            #Real image
            image_batch =X_train[np.random.randint(low=0,high=X_train.shape[0],size=batch_size)]
            
            #Concatenate with generated ones
            X= np.concatenate([image_batch, fake_image])
            
            # Labels for generated and real data (0 for fake, 1 for real)
            y_dis=np.zeros(2*batch_size)
            y_dis[:batch_size]=1
            
            #Train discriminator
            disc.trainable=True  #unfreeze the layers of discriminator
            disc.train_on_batch(X, y_dis)
            
            #Tricking generator
            y_gen = np.ones(batch_size)
            noise = create_noise(batch_size)
            
            #freezing layers of gan while training generator
            discriminator.trainable=False
            
            gan.train_on_batch(noise, y_gen)
        if i == 1 or i % 10 == 0:
            plot_generated_images(i, gen)

In [ ]:
training()

  0%|                                                                                          | 0/128 [00:00<?, ?it/s]

(128, 784)


c:\users\i353565\appdata\local\programs\python\python36\lib\site-packages\keras\engine\training.py:493: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'
  1%|▋                                                                                 | 1/128 [00:03<07:50,  3.71s/it]

(128, 784)


  2%|█▎                                                                                | 2/128 [00:03<05:32,  2.64s/it]

...

(128, 784)


 16%|████████████▋                                                                    | 20/128 [00:04<00:26,  4.02it/s]

(128, 784)


 16%|█████████████▎                                                                   | 21/128 [00:05<00:27,  3.96it/s]

(128, 784)
